# App for Dataviz

In [1]:

import dash
from jupyter_dash import JupyterDash
from dash import dcc
from dash import html
from dash.dependencies import Input, Output, State
from dash.exceptions import PreventUpdate
import plotly.express as px
import plotly.colors as pc
import pandas as pd
import numpy as np
import math

## import data

In [2]:
# read dataframe (preprocessed in main.ipynb)
df = pd.read_csv("data/merged_data_clean.csv").drop(columns = "Unnamed: 0")
# df = df.replace("Eswatini","Swaziland")
df

Country Code  Year  Deaths from HIV/AIDS in 100 thousand people  \
0      Algeria  DZA  1990                                     0.205573   
1      Algeria  DZA  1991                                     0.227273   
2      Algeria  DZA  1992                                     0.250077   
3      Algeria  DZA  1993                                     0.274849   
4      Algeria  DZA  1994                                     0.300538   
...        ...  ...   ...                                          ...   
1615  Zimbabwe  ZWE  2015                                   271.838069   
1616  Zimbabwe  ZWE  2016                                   249.251170   
1617  Zimbabwe  ZWE  2017                                   223.703501   
1618  Zimbabwe  ZWE  2018                                   196.301602   
1619  Zimbabwe  ZWE  2019                                   180.620329   

      Life expectancy   Cardiovascular diseases   Neoplasms   Drowning  \
0              66.938                 34.788700    6.872654   0.786121   
1              67.270                 35.784980    7.135730   0.743511   
2              67.575                 36.557049    7.258288   0.724943   
3              67.877                 37.300950    7.379766   0.709279   
4              68.194                 37.682038    7.416182   0.693864   
...               ...                       ...         ...        ...   
1615           59.534                 12.505176    8.380066   0.578121   
1616           60.294                 12.912334    8.736636   0.611032   
1617           60.812                 13.285884    9.073112   0.632819   
1618           61.195                 13.791937    9.502992   0.651582   
1619           61.490                 14.061202    9.746106   0.653096   

       Maternal disorders   Chronic respiratory diseases  ...  \
0                1.061368                       2.868667  ...   
1                1.005819                       2.931052  ...   
2                0.963743                       2.978710  ...   
3                0.920274                       3.027255  ...   
4                0.863998                       3.045583  ...   
...                   ...                            ...  ...   
1615             1.015002                       2.067063  ...   
1616             1.016606                       2.126924  ...   
1617             1.010809                       2.180040  ...   
1618             1.018363                       2.251893  ...   
1619             1.017424                       2.283885  ...   

       Parkinson's disease   HIV/AIDS   Acute hepatitis   Self-harm   Malaria  \
0                 0.285699   0.028929          0.316547    0.913479  0.006069   
1                 0.295107   0.032961          0.313160    0.907066  0.005981   
2                 0.306105   0.037050          0.307857    0.915418  0.007695   
3                 0.316808   0.041575          0.305150    0.925577  0.007557   
4                 0.324835   0.045823          0.299757    0.939737  0.005330   
...                    ...        ...               ...         ...       ...   
1615              0.161946  21.964689          0.109622    1.676438  1.894479   
1616              0.167307  20.769693          0.111208    1.747906  1.566541   
1617              0.172457  19.294984          0.111391    1.804474  1.638591   
1618              0.179517  17.556091          0.109639    1.870430  1.652881   
1619              0.183245  16.458611          0.107482    1.893108  1.634642   

       Interpersonal violence   Nutritional deficiencies   Meningitis  \
0                    0.319370                   0.295142     0.546060   
1                    0.316442                   0.287364     0.520021   
2                    0.323609                   0.278729     0.498172   
3                    0.332118                   0.270976     0.478206   
4                    0.352809                   0.257013     0.452600   
...                       ...        

## Modify Data

In [3]:
# create lookup table for bar chart
iso3_countrynames = pd.DataFrame()
iso3_countrynames["Code"] = df["Code"].unique()
iso3_countrynames["Country"] = df["Country"].unique()
iso3_countrynames

Code                       Country
0   DZA                       Algeria
1   AGO                        Angola
2   BEN                         Benin
3   BWA                      Botswana
4   BFA                  Burkina Faso
5   BDI                       Burundi
6   CMR                      Cameroon
7   CPV                    Cape Verde
8   CAF      Central African Republic
9   TCD                          Chad
10  COM                       Comoros
11  COG                         Congo
12  CIV                 Cote d'Ivoire
13  COD  Democratic Republic of Congo
14  DJI                      Djibouti
15  EGY                         Egypt
16  GNQ             Equatorial Guinea
17  ERI                       Eritrea
18  SWZ                      Eswatini
19  ETH                      Ethiopia
20  GAB                         Gabon
21  GMB                        Gambia
22  GHA                         Ghana
23  GIN                        Guinea
24  GNB                 Guinea-Bissau
25  KEN                         Kenya
26  LSO                       Lesotho
27  LBR                       Liberia
28  LBY                         Libya
29  MDG                    Madagascar
30  MWI                        Malawi
31  MLI                          Mali
32  MRT                    Mauritania
33  MUS                     Mauritius
34  MAR                       Morocco
35  MOZ                    Mozambique
36  NAM                       Namibia
37  NER                         Niger
38  NGA                       Nigeria
39  RWA                        Rwanda
40  STP         Sao Tome and Principe
41  SEN                       Senegal
42  SYC                    Seychelles
43  SLE                  Sierra Leone
44  SOM                       Somalia
45  ZAF                  South Africa
46  SSD                   South Sudan
47  SDN                         Sudan
48  TZA                      Tanzania
49  TGO                          Togo
50  TUN                       Tunisia
51  UGA                        Uganda
52  ZMB                        Zambia
53  ZWE                      Zimbabwe

## Load Geojson data

In [4]:
# source: https://public.opendatasoft.com/explore/dataset/country_shapes/export/ 
import geojson
with open("data/country_shapes.geojson") as f:
    gj = geojson.load(f)
gj.get
gj

{"features": [{"geometry": {"coordinates": [[[[114.095078, 4.590538], [114.101646, 4.591388], [114.139977, 4.594166], [114.160538, 4.594166], [114.179703, 4.592777], [114.190536, 4.589999], [114.203049, 4.581666], [114.286919, 4.59236], [114.300812, 4.595554], [114.520264, 4.69111], [114.52916, 4.695832], [114.544983, 4.7075], [114.555252, 4.717777], [114.564148, 4.729444], [114.579987, 4.747777], [114.592758, 4.762221], [114.633881, 4.803054], [114.655258, 4.822777], [114.666092, 4.8325], [114.685532, 4.847499], [114.716927, 4.871387], [114.736649, 4.885833], [114.913597, 4.996387], [114.931374, 5.005833], [114.954163, 5.017499], [114.963608, 5.021666], [115.00943, 5.037221], [115.040268, 5.047499], [115.051376, 5.050277], [115.069153, 5.053054], [115.082207, 5.052221], [115.098038, 5.047499], [115.1036, 5.039096], [115.041656, 4.968888], [114.9897, 4.904721], [114.982063, 4.889721], [115.018433, 4.895795], [114.989143, 4.842916], [114.979431, 4.831666], [114.962196, 4.821944], [114.9

## Color maps

In [5]:
country_zipper = zip(df["Country"].unique(), pc.sample_colorscale("turbo", df["Country"].unique().size))
color_map_country = dict(country_zipper)
cause_zipper = zip(df.iloc[0, 5:].index.values,  pc.sample_colorscale("rainbow", df.iloc[0, 5:].index.values.size))
color_map_cause = dict(cause_zipper)

## Create App

In [6]:
# define color scheme
colors = {
    'background': 'black',
    'text': 'white',
    'highlight':'yellow'
}
darkScheme ={
    'backgroundColor':colors['background'],
    'color': colors['text']
}
# define hover style
hoverStyle = dict(
        bgcolor="white",
        font_size=16,
        font_family="Rockwell"
    )

In [7]:
# the variable that holds our final webAPP
app = JupyterDash(__name__)

# create our map with animations already built in
chloropleth = px.choropleth(
        df,
        geojson=gj,
        color="Deaths from HIV/AIDS in 100 thousand people",
        locations="Code",
        featureidkey="properties.cou_iso3_code",
        projection="mercator",
        animation_frame="Year", 
        animation_group="Country",
        range_color=[df['Deaths from HIV/AIDS in 100 thousand people'].min(), df["Deaths from HIV/AIDS in 100 thousand people"].max()],
        hover_name=df["Year"].astype(str) + " " +  df["Country"],
        hover_data={"Deaths from HIV/AIDS in 100 thousand people" : ":.1f",
                        "Life expectancy": ":.1f",
                        "Code":False,
                        "Year":False,
                        "Country":False},
        custom_data=["Code"],
        color_continuous_scale='reds'
        )
# chloropleth.update_traces(colorbar_orientation='h', selector=dict(type='chloropleth'))
chloropleth.update_coloraxes(
        colorbar_thicknessmode="pixels",
        colorbar_orientation='h',
        colorbar_thickness=10,
        colorbar_lenmode="fraction",
        colorbar_len=0.5
)
chloropleth.update_geos(fitbounds="locations", visible=False)
chloropleth.update_layout(margin={"r":0,"t":0,"l":0,"b":0},
                             autosize = True)





# here we define the layout and components of our app
app.layout = html.Div([
    #  africa map container
    html.Div([
        html.H1("HIV deaths per 100 Thousand people:", style={'width':'100vw',
                                                                'height':'auto',
                                                                'textAlign': 'center'
                                                                }), # heading
        dcc.Graph(id="chloropleth", config={"displayModeBar": False, "showTips": False},
                                    figure=chloropleth, style={'width': '60vw',
                                                                    'height': '85vh',
                                                                    'display':'inline-block',
                                                                    'verticalAlign':'top'}), # africa map figure with id "chloropleth"
        html.P(
            "Text bezeichnet im nichtwissenschaftlichen Sprachgebrauch eine abgegrenzte, zusammenhängende, meist schriftliche sprachliche Äußerung, im weiteren Sinne auch nicht geschriebene, aber schreibbare Sprachinformation. Aus sprachwissenschaftlicher Sicht sind Texte die sprachliche Form einer kommunikativen Handlung.",
            style={
                    'margin':10,
                    'width': '25vw',
                    'height': '85vh',
                    'display':'inline-block',
                    'fontSize':'150%',
                    'padding':10,
                    'verticalAlign':'middle'
            }
        )
    ], style={
        'width': '100vw',
        'height':'100vh',
        'margin':'20px',
        'verticalAlign':'top'}),
    # dropdown for country selection
    html.Div([
        html.Div(dcc.Dropdown(
                            id='country_select',
                            options=[{'label': code, 'value': country} for index, country, code in iso3_countrynames.itertuples()],
                            multi=True
                        ), style={
                            'margin':'20px',
                            'height': 'auto',
                            'width': '45vw'
                        }),
            # graph (later for the wormgraph)
            html.Div([dcc.Graph(id="worm_figure", style={
                                                    'margin': '20px 20px 20px 20px',
                                                    'display': 'inline-block',
                                                    'height':'70vh',
                                                    'width':'45vw'},
                                                    config={"displayModeBar": False, "showTips": False}),
                    dcc.Graph(id="bar_chart", style={
                                                    'margin': '20px 20px 20px 20px',
                                                    'display': 'inline-block',
                                                    'height':'70vh',
                                                    'width':'45vw'},
                                                    config={"displayModeBar": False, "showTips": False})])
                    ], style={'width':'100vw',
                            'height':'100vh',
                            'padding':'0px',
                            'margin':'10px'})
    ], style={
        'height':'200vh',
        'width':'100vw',
        'font':'Verdana'
    })
  

## Create Callbacks

In [8]:
# here we define the functionality and interactivity of our App
# define input and output of callback function
@app.callback(
    # Output("choropleth", "figure"),
    Output("worm_figure", "figure"),
    # Output("worm_container", "style"),
    Input("country_select", "value"))
    # the callback function: called when a value of the defined inputs above changes.
def display_choropleth(country_select):
    # if no countries are selected
    if(not country_select):
       raise PreventUpdate

    # select df
    df_temp = df[df["Code"].isin(country_select)]
    # create worm graph
    fig2 = px.scatter(df_temp,
                            x="Year",
                            y="Life expectancy",
                            color="Country",
                            color_discrete_map= color_map_country,
                            hover_name=df_temp["Year"].astype(str)+ " " + df_temp["Country"],
                            hover_data={"Deaths from HIV/AIDS in 100 thousand people" : ":.1f",
                                        "Life expectancy": ":.1f",
                                        "Code":False,
                                        "Year":False,
                                        "Country":False},
                            custom_data=["Code","Year","Country"],
                            size = 'Deaths from HIV/AIDS in 100 thousand people',
                            size_max = df["Deaths from HIV/AIDS in 100 thousand people"].max()/30
                            )
    fig2.update_layout(margin={"r":0,"t":0,"l":0,"b":0},
                            legend=dict(
                                orientation="h",
                                yanchor="bottom",
                                y=1.02,
                                xanchor="left",
                                x=0
                            ))
    fig2.update_yaxes(range=[df["Life expectancy"].min(), df["Life expectancy"].max()])
    fig2.update_traces(marker = dict(
        sizemode='area',
        sizemin=1,
        )
    )
    fig2.show(config={"displayModeBar": False, "showTips": False})
        # marker_size = 0.1 * df_temp['Deaths from HIV/AIDS in 100 thousand people'])

    return fig2

In [9]:
# here we define the functionality and interactivity of our App
# define input and output of callback function
@app.callback(
    # Output("choropleth", "figure"),
    Output("country_select", "value"),
    # Output("worm_container", "style"),
    Input("chloropleth", "clickData"),
    State("country_select", "value"))
# the callback function: called when a value of the defined inputs above changes.
def click_callback(clickData, country_select):
    # worm_style = {'display', 'block'}
    # if any countries are selected
    if(not clickData):
        raise PreventUpdate
    if(not country_select):
        selection = clickData["points"][0]["customdata"]
    else:
        # concatenate lists
        selection = country_select + clickData["points"][0]["customdata"]
        # remove duplicates
        selection = pd.Series(selection).unique()
    return selection


In [10]:
# Create a color vector for causes of death
# colorDf = pd.DataFrame()
# colorDf["column"] = df.iloc[0, 5:].index.values
# colorDf["color"] = pc.sample_colorscale("reds", colorDf["column"].size)

# here we define the functionality and interactivity of our App
# define input and output of callback function
@app.callback(
    Output("bar_chart", "figure"),
    Input("worm_figure", "hoverData"))# the callback function: called when a value of the defined inputs above changes.
def hover_bar_chart(hoverData):
    # worm_style = {'display', 'block'}
    # if any countries are selected
    if(not hoverData):
        raise PreventUpdate
    else:
        # return bar chart
        data_selection = df[(df["Year"] == hoverData["points"][0]["customdata"][1]) &
                            (df["Code"] == hoverData["points"][0]["customdata"][0])]
        subSelection = data_selection.iloc[0, 5:].sort_values(ascending=False).head(10)
        barFig = px.bar(
            x = subSelection.index.values,
            y = subSelection,
            color = subSelection.index.values,
            color_discrete_map= color_map_cause,
            title=("Top 10 causes of death in " +
                    str(hoverData["points"][0]["customdata"][1]) +
                    " in " +
                    hoverData["points"][0]["customdata"][2] +
                    " in Percent.")
        )
        barFig.update_layout(showlegend=False,
                            yaxis_title = "Percentage of total deaths",
                            xaxis_title = "Cause of death"
                            )
        barFig.update_yaxes(range=[0, 70])
        barFig.show(config={"displayModeBar": False, "showTips": False})

    return barFig


## RUN APP Server

In [11]:
# run the local server
# visit http://127.0.0.1:8050/ in webbrowser to see results and error codes
app.run_server(debug=True)

Dash app running on http://127.0.0.1:8050/


Possible deployment:
https://austinlasseter.medium.com/how-to-deploy-a-simple-plotly-dash-app-to-heroku-622a2216eb73 